In [ ]:
# label transfer with Seurat?

In [2]:
library(Seurat)
library(dplyr)
library(ggplot2)
library(SingleCellExperiment)

In [3]:
# load reference
heart.ref = readRDS('~/septation/markers/Mantri/Mantri_chicken_heart.rds')

In [4]:
# list of stages and samples
stages = rep(c('stage9', 'stage13', 'stage16'), each = 3)
samples = paste0('sample', rep(1:3, 3))

In [5]:
# load list of orthologs
om = read.delim('lizard_chicken_orthologs_eggNOG.txt', sep = '\t')
om <- om[!is.na(om$lizard_gene) & !is.na(om$ortholog_name),]
dim(om)
om[1,]

[1] 25708     7

query          orth_type species             orthologs          lizard_gene
1 XP_060608688.1 one2one   Gallus gallus(9031) ENSGALP00000026323 ARHGEF10   
  ortholog_gene      ortholog_name
1 ENSGALG00000016350 ARHGEF10

In [6]:
# load data
pb = txtProgressBar(min = 0, max = length(samples), initial = 0)

for(sampleid in 1:length(samples)){
    file0 = paste0(stages[sampleid], '_', samples[sampleid], '_data.rds')
    sce = readRDS(file0)

    # subset to mouse 1-1 orthologs
    genelist <- om$ortholog_name[match(rownames(sce), om$lizard_gene)]
    # genelist[1:10]
    
    exp_mat2 = LayerData(sce, assay = 'RNA', layer = 'counts')
    mtd2 = sce@meta.data
    rownames(exp_mat2) = genelist
    exp_mat2 <- exp_mat2[!is.na(rownames(exp_mat2)) & rownames(exp_mat2)!='',]
    exp_mat2 <- exp_mat2[!(duplicated(rownames(exp_mat2))),]

    # dim(exp_mat2)
    heart.query = CreateSeuratObject(counts = exp_mat2, meta.data = mtd2)

    # select two technologies for the query datasets
    heart.query <- NormalizeData(heart.query)
    heart.anchors <- FindTransferAnchors(reference = heart.ref, query = heart.query, dims = 1:30,
        reference.reduction = "pca")
    
    # get both levels of anno
    predictions <- TransferData(anchorset = heart.anchors, refdata = heart.ref$celltypes.0.5, dims = 1:30)
    heart.query <- AddMetaData(heart.query, metadata = predictions)
    
    # add predictions to data.frame to save
    newdf = data.frame(barcode = rownames(heart.query@meta.data), class = heart.query$predicted.id,
                      class_prob = heart.query$prediction.score.max)
    # newdf[1:3,]

    # save
    write.table(newdf, file = paste0('annotations/', stages[sampleid], '_', samples[sampleid], '_Mantri_Seurat_label_transfer.csv'), 
                sep = ',', row.names = F, col.names = T, quote = F)

    setTxtProgressBar(pb, sampleid)
}

Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 1895 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 3727 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 3102 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 1976 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 3198 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2208 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2852 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 3468 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2725 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

